# DATA GATHERING

# Data from Musicbrainz.org

## 1) Artist information

In [2]:
import pandas as pd
import numpy as np
#import time
#!pip install pygeocoder
#from pygeocoder import Geocoder #If you want to follow the geocoding later, you will need your own Google Maps API key
#import matplotlib.pyplot as plt
#%matplotlib inline
from tqdm import tqdm

In [3]:
artists= pd.read_csv('Musicbrainz/Tables_used/artist.txt',sep='\t', header=None, engine='c', usecols=[0,1,2,11,17])
artists.columns = ['artist_id','artist_mbid','artist_name','start_area1', 'start_area2']
artists.head()

artist_id                           artist_mbid      artist_name  \
0     805192  8972b1c1-6482-4750-b51f-596d2edea8b1            WIK▲N   
1     371203  49add228-eac5-4de8-836c-d75cde7369c3      Pete Moutso   
2     273232  c112a400-af49-4665-8bba-741531d962a1          Zachary   
3     101060  ca3f3ee1-c4a7-4bac-a16a-0b888a396c6b  The Silhouettes   
4     145773  7b4a548e-a01a-49b7-82e7-b49efeb9732c     Aric Leavitt   

   start_area1  start_area2  
0          NaN          NaN  
1          NaN          NaN  
2          NaN          NaN  
3        222.0       7707.0  
4          NaN          NaN

In [4]:
#Let's see how many artists we have:
artists['artist_id'].nunique()

1476425

In [5]:
#How much info we have for each artist?
artists.isnull().sum(axis=0)

artist_id            0
artist_mbid          0
artist_name          8
start_area1     808442
start_area2    1274001
dtype: int64

What are the "start_area1" and "start_area2"? If we look at Musicbrainz's field description for each artist (https://musicbrainz.org/doc/Artist), we can see that:

Area: The artist area, as the name suggests, indicates the area with which an artist is primarily identified with. It is often, but not always, its birth/formation country.

We will keep this information as the artist's origin for later.

We need to incorporate as well the table called "artist credit", which gives us the artist credit_id. We will use this field to join later on each release with its artist:

In [6]:
artists_credit= pd.read_csv('Musicbrainz/Tables_used/artist_credit_name.txt',sep='\t', header=None, engine='c', usecols=[0,2,3])
artists_credit.columns = ['credit_id','artist_id','artist_name']
artists_credit.head()

credit_id  artist_id             artist_name
0     578352     578352           Gustav Ruppke
1     273232     273232                 Zachary
2     153193     153193  The High Level Ranters
3      32262      32262        Georges Brassens
4    1389968    1171184    Harvard of the South

In [7]:
#Let's join the artists with their credit id and verify that the matching is good:
df = pd.merge(artists, artists_credit, how='left', on='artist_id')
df.head()

artist_id                           artist_mbid    artist_name_x  \
0     805192  8972b1c1-6482-4750-b51f-596d2edea8b1            WIK▲N   
1     371203  49add228-eac5-4de8-836c-d75cde7369c3      Pete Moutso   
2     273232  c112a400-af49-4665-8bba-741531d962a1          Zachary   
3     101060  ca3f3ee1-c4a7-4bac-a16a-0b888a396c6b  The Silhouettes   
4     145773  7b4a548e-a01a-49b7-82e7-b49efeb9732c     Aric Leavitt   

   start_area1  start_area2  credit_id    artist_name_y  
0          NaN          NaN   822846.0            WIK▲N  
1          NaN          NaN        NaN              NaN  
2          NaN          NaN   273232.0          Zachary  
3        222.0       7707.0   101060.0  The Silhouettes  
4          NaN          NaN   145773.0     Aric Leavitt

In [8]:
#It looks like it makes sense. Please note that the credit id is sometimes equal to the artist_id, but not always:
df['check'] = df['artist_id'] - df['credit_id']
df['check'].nunique()

1270628

In [9]:
df.isnull().sum(axis=0)

artist_id              0
artist_mbid            0
artist_name_x         15
start_area1      1120376
start_area2      2109027
credit_id         461241
artist_name_y     461253
check             461241
dtype: int64

In [10]:
#We can now get rid of check and the duplicate artist_name column:
df.drop(labels=['check','artist_name_y'], axis=1, inplace=True)
df.head()

artist_id                           artist_mbid    artist_name_x  \
0     805192  8972b1c1-6482-4750-b51f-596d2edea8b1            WIK▲N   
1     371203  49add228-eac5-4de8-836c-d75cde7369c3      Pete Moutso   
2     273232  c112a400-af49-4665-8bba-741531d962a1          Zachary   
3     101060  ca3f3ee1-c4a7-4bac-a16a-0b888a396c6b  The Silhouettes   
4     145773  7b4a548e-a01a-49b7-82e7-b49efeb9732c     Aric Leavitt   

   start_area1  start_area2  credit_id  
0          NaN          NaN   822846.0  
1          NaN          NaN        NaN  
2          NaN          NaN   273232.0  
3        222.0       7707.0   101060.0  
4          NaN          NaN   145773.0

## 2) Release information

The objective of this project is to visualize when each artist released for the first time a certain CD/Album/Single etc.

If we look at the "releases" table:

In [11]:
releases = pd.read_csv('Musicbrainz/Tables_used/release.txt',sep='\t', header=None, engine='c', usecols=[0,2,3,4])
releases.columns = ['release_id','release_group','credit_id','group_id']
releases.head()

release_id           release_group  credit_id  group_id
0           9       A Sorta Fairytale         60    896742
1          10       A Sorta Fairytale         60    896742
2          11       Glory of the 80's         60     95360
3          12  Silent All These Years         60    104189
4          26                  Demons      20211     94299

We can see, in the first 2 rows, that the same CD/Album can be released/remastered many times. According to Musicbrainz's field description for each release (https://musicbrainz.org/doc/Release):

"A MusicBrainz release represents the unique release (i.e. issuing) of a product on a specific date with specific release information such as the country, label, barcode and packaging. If you walk into a store and purchase an album or single, they are each represented in MusicBrainz as one release".

If we look at another release-related field in Musicbrainz, we find the "release group" (https://musicbrainz.org/doc/Release_Group):

"A release group, just as the name suggests, is used to group several different releases into a single logical entity. Every release belongs to one, and only one release group.

Both release groups and releases are "albums" in a general sense, but with an important difference: a release is something you can buy as media such as a CD or a vinyl record, while a release group embraces the overall concept of an album -- it doesn't matter how many CDs or editions/versions it had."

By reading these descriptions, we can clearly see that the release group is the table we are looking for as it represents a single creation, no matter how many times it has been edited or released afterwards. So we will have to keep the first release id for each release group.

In [12]:
release_country = pd.read_csv('Musicbrainz/Tables_used/release_country.txt',sep='\t', header=None, engine='c', usecols=[0,1,2])
release_country.columns = ['release_id','area_id','release_year']
release_country.head()

release_id  area_id  release_year
0           3       81        1997.0
1     1427792      107        2014.0
2           9       81        2002.0
3          10      221        2002.0
4          11       81        1999.0

In [13]:
df2 = pd.merge(releases, release_country, how='left', on='release_id')
df2.head()

release_id           release_group  credit_id  group_id  area_id  \
0           9       A Sorta Fairytale         60    896742     81.0   
1          10       A Sorta Fairytale         60    896742    221.0   
2          11       Glory of the 80's         60     95360     81.0   
3          12  Silent All These Years         60    104189     81.0   
4          26                  Demons      20211     94299    107.0   

   release_year  
0        2002.0  
1        2002.0  
2        1999.0  
3        1997.0  
4        1998.0

In [14]:
#Let's see how many releases we have:
df2['release_id'].nunique()

2198457

In [15]:
df2.isnull().sum(axis=0)

release_id            0
release_group         7
credit_id             0
group_id              0
area_id          287376
release_year     341983
dtype: int64

In [16]:
#We want to keep only the releases which have a release year, so we can drop the others:
df2.dropna(subset=['release_year'], axis=0, inplace=True)
df2['release_year'] = df2.release_year.astype(int,inplace=True)
df2['release_id'].nunique()

1859982

In [17]:
#Let's analyze the year column:
pd.options.display.max_rows = 2000
df2.groupby('release_year').count()

release_id  release_group  credit_id  group_id  area_id
release_year                                                         
1                      2              2          2         2        2
4                      1              1          1         1        1
5                      5              5          5         5        5
7                      1              1          1         1        1
8                      2              2          2         2        2
10                     3              3          3         3        3
14                     1              1          1         1        1
17                     4              4          4         4        4
18                     1              1          1         1        1
19                     3              3          3         3        3
20                     2              2          2         2        2
21                     1              1          1         1        1
23                     1              1          1         1        1
24                     1              1          1         1        1
25                     2              2          2         2        2
28                     2              2          2         2        2
29                     2              2          2         2        2
31                     2              2          2         2        2
73                     1              1          1         1        1
195                    1              1          1         1        1
198                    1              1          1         1        1
199                    2              2          2         2        2
200                    4              4          4         4        4
201                    4              4          4         4        4
209                    2              2          2         2        2
666                    1              1          1         1        1
701                    1              1          1         1        1
996                    1              1          1         1        1
1009                   1              1          1         1        1
1029                   1              1          1         1        1
1198                   1              1          1         1        1
1694                   1              1          1         1        1
1886                   1              1          1         1        1
1889                   1              1          1         1        1
1890                 249            249        249       249      249
1891                  11             11         11        11       11
1892                 130            130        130       130      130
1893                 183            183        183       183      183
1894                  29             29         29        29       29
1895                   2              2          2         2        2
1896                   6              6          6         6        6
1897                  65             65         65        65       65
1898                 183            183        183       183      183
1899                 281            281        281       281      281
1900                 131            131        131       131      131
1901                 199            199        199       199      199
1902                 234            234        234       234      234
1903                 196            196        196       196      196
1904                 155            155        155       155      155
1905                 163            163        163       163      163
1906                 154            154        154       154      154
1907                 171            171        171       171      171
1908                 212            212        212       212      212
1909                 187            187        187       187      187
1910                 115            115        115       115      115
1911                  54

By looking at the different year values, and, in order to have enough values per year, we could drop the rows whose year is below 1890 and above 2019. Our visualization would have 130 years, which is pretty good.

In [18]:
df2.drop(df2[df2['release_year'] < 1890].index , inplace=True)
df2.drop(df2[df2['release_year'] >2019].index , inplace=True)
df2.sort_values(by=['release_year']).head()

release_id                  release_group  credit_id  group_id  \
1266766      386919      Visions of Paradise Waltz      97546    712605   
1266956      386830  German Ballad with Variations      97546    712514   
1266958      386829  German Ballad with Variations      97546    712514   
1266960      386828           Mountain Bells Polka      97546    712513   
1266961      386827           Mountain Bells Polka      97546    712513   

         area_id  release_year  
1266766    222.0          1890  
1266956    222.0          1890  
1266958    222.0          1890  
1266960    222.0          1890  
1266961    222.0          1890

In [19]:
#Converting the year column to datetime for later:
df2['release_year'] = pd.to_datetime(df2['release_year'].astype(str), format='%Y')
df2.dtypes

release_id                int64
release_group            object
credit_id                 int64
group_id                  int64
area_id                 float64
release_year     datetime64[ns]
dtype: object

In [20]:
#We sort by release id and year (we could have 2 release groups with the same name but produced by different artists):
df2.sort_values(['release_group','release_year','credit_id'], ascending=[True,True,True], inplace=True)
df2.head()

release_id            release_group  credit_id  group_id  area_id  \
2026273     2163750                             2205562   1962329    240.0   
1648516     1846605                             1503027   1713833    240.0   
1250325     1714060    Beaux Soirs De Paris     1324142   1609358     73.0   
2116340     2265346                    Le 1     2291833   2042812    240.0   
1748061     1895266   M2Music HitDisc Vol. 1          1   1751021    222.0   

        release_year  
2026273   2014-01-01  
1648516   2015-01-01  
1250325   1995-01-01  
2116340   2018-01-01  
1748061   2006-01-01

In [21]:
df2[df2['release_group'] == 'Artaxerxes']

release_id release_group  credit_id  group_id  area_id release_year
1836724     2378622    Artaxerxes    2392005   2132682    240.0   1996-01-01
1910376     2379252    Artaxerxes    2392005   2132682    221.0   2009-01-01
1909444     2379244    Artaxerxes    2392011   2133192    222.0   2011-01-01

In [22]:
#Now we can delete the duplicate releases and keep the ones who were first released:
df2.drop_duplicates(subset=['release_group','credit_id'],keep='first', inplace=True)
df2['release_id'].nunique()

1499614

In [23]:
#Just to double-check:
df2[df2['release_group'] == 'Artaxerxes']

release_id release_group  credit_id  group_id  area_id release_year
1836724     2378622    Artaxerxes    2392005   2132682    240.0   1996-01-01
1909444     2379244    Artaxerxes    2392011   2133192    222.0   2011-01-01

## 3) Matching releases with artists

Now that we have both artist and releases dataframes, we can join them:

In [24]:
df3 = pd.merge(df2, df, how='left', on='credit_id')
df3.head()

release_id            release_group  credit_id  group_id  area_id  \
0     2163750                             2205562   1962329    240.0   
1     1846605                             1503027   1713833    240.0   
2     1714060    Beaux Soirs De Paris     1324142   1609358     73.0   
3     2265346                    Le 1     2291833   2042812    240.0   
4     1895266   M2Music HitDisc Vol. 1          1   1751021    222.0   

  release_year  artist_id                           artist_mbid  \
0   2014-01-01  1654312.0  d10d6441-dcc1-4202-93bf-0c0acf72913a   
1   2015-01-01  1112115.0  7b52c77b-1a34-439d-a285-3a7c69cb5b1a   
2   1995-01-01  1122795.0  71b8451c-c10a-400e-9544-101f34ab2522   
3   2018-01-01  1720981.0  a69efb5f-0b28-4328-8ff0-44d8d6f39755   
4   2006-01-01        1.0  89ad4ac3-39f7-470e-963a-56509c546377   

     artist_name_x  start_area1  start_area2  
0         Soul Glo       7707.0          NaN  
1      Ben Bennett          NaN          NaN  
2  Soixante Étages          NaN          NaN  
3         TedeuzeM      68613.0          NaN  
4  Various Artists          NaN          NaN

In [25]:
df3.isnull().sum(axis=0)

release_id            0
release_group         4
credit_id             0
group_id              0
area_id               0
release_year          0
artist_id           151
artist_mbid         151
artist_name_x       155
start_area1      430452
start_area2      959581
dtype: int64

In [26]:
df3['release_id'].nunique()

1499614

In [27]:
len(df3)

1724524

In [28]:
df3[df3['release_group']=='Artaxerxes']

release_id release_group  credit_id  group_id  area_id release_year  \
119493     2378622    Artaxerxes    2392005   2132682    240.0   1996-01-01   
119494     2378622    Artaxerxes    2392005   2132682    240.0   1996-01-01   
119495     2378622    Artaxerxes    2392005   2132682    240.0   1996-01-01   
119496     2378622    Artaxerxes    2392005   2132682    240.0   1996-01-01   
119497     2378622    Artaxerxes    2392005   2132682    240.0   1996-01-01   
119498     2378622    Artaxerxes    2392005   2132682    240.0   1996-01-01   
119499     2378622    Artaxerxes    2392005   2132682    240.0   1996-01-01   
119500     2378622    Artaxerxes    2392005   2132682    240.0   1996-01-01   
119501     2378622    Artaxerxes    2392005   2132682    240.0   1996-01-01   
119502     2379244    Artaxerxes    2392011   2133192    222.0   2011-01-01   
119503     2379244    Artaxerxes    2392011   2133192    222.0   2011-01-01   
119504     2379244    Artaxerxes    2392011   2133192    222.0   2011-01-01   

        artist_id                           artist_mbid  \
119493   391603.0  e3062782-ab7b-41bc-8e65-aeea16dc1a89   
119494   124232.0  4e7f1926-8704-4545-a1a1-ded91651c884   
119495   688791.0  f34e9da4-2ee7-4f27-aa34-adc5db791bec   
119496  1129787.0  c33f733e-2bf4-402b-9455-1a293601a1cd   
119497  1104538.0  5680c729-615b-47e2-969e-27a087c572fb   
119498   402986.0  70af5d9a-c6e0-4fcf-9cde-4d3d00e0fcb0   
119499   183632.0  954d1c83-259f-4a25-8878-10c19bb097af   
119500    87510.0  857588a5-b7aa-4f72-a87b-8f03dca60e30   
119501  1078968.0  93da7aaa-250b-46e1-b5ef-0ad78d46dc3f   
119502   854064.0  a87f2b39-84c7-4888-935c-d41943bd7971   
119503   124232.0  4e7f1926-8704-4545-a1a1-ded91651c884   
119504   989288.0  4c05f6e6-7a40-437e-9f12-a90c1da7b4f8   

                    artist_name_x  start_area1  start_area2  
119493              Ian Partridge        221.0       1178.0  
119494                Thomas Arne        221.0       1178.0  
119495         Christopher Robson          NaN          NaN  
119496            Patricia Spence          NaN          NaN  
119497              Philippa Hyde        221.0          NaN  
119498  The Parley of Instruments        221.0       1178.0  
119499             Catherine Bott        221.0          NaN  
119500                Roy Goodman        221.0      30926.0  
119501       Richard Edgar‐Wilson          NaN          NaN  
119502    Classical Opera Company        221.0          NaN  
119503                Thomas Arne        221.0       1178.0  
119504                   Ian Page        221.0          NaN

If we look at the above, we can see that there is one line per each artist that participated for each release ID.

As we don't want to show duplicate releases, we need to keep only one artist per release. We will keep the first artist appearing for each release (even though we know this is not 100% accurate, but we have to avoid duplicates). This will afftect 224.910 rows under a total of 1.499.614 unique releases, so 14% of our dataset.

In [29]:
#Now we can delete the duplicate releases and keep the ones who were first released:
df3.drop_duplicates(subset=['release_id'],keep='first', inplace=True)
df3['release_id'].nunique()

1499614

In [30]:
len(df3)

1499614

## 4) Geographical data

The idea of the visualization is to see where each gender comes from, so, ideally, we would have to look at the artists origins (start area: last 2 columns of our dataframe).

In our dataframe df3, the 5th column "area_id" is related to the area where the release was produced. This isn't directly related to the origin of an artist/band, as many artists have to record their works in different countries/or areas.

Let's see for how many releases we have that information:

In [31]:
df3.isnull().sum(axis=0)

release_id            0
release_group         4
credit_id             0
group_id              0
area_id               0
release_year          0
artist_id           151
artist_mbid         151
artist_name_x       155
start_area1      404503
start_area2      876562
dtype: int64

In Musicbrainz's database, we have some tables related to the areas. Let's see how we can use them to input more geographical information into our dataframe:

In [32]:
areas = pd.read_csv('Musicbrainz/Tables_used/area.txt',sep='\t', header=None, engine='python', usecols=[0,2,3])
areas.columns = ['area_id','area_name','code_type']
areas.head()

area_id area_name  code_type
0    15449   Greccio        4.0
1       38    Canada        1.0
2       43     Chile        1.0
3       44     China        1.0
4       36  Cambodia        1.0

In [33]:
#Let's see the area types we have:
area_types = pd.read_csv('Musicbrainz/Tables_used/area_type.txt',sep='\t', header=None, engine='python', usecols=[1,3,4], error_bad_lines=False)
area_types.columns = ['type','code_type','definition']
area_types.head(20)

type  code_type                                         definition
0       Country          1  Country is used for areas included (or previou...
1   Subdivision          2  Subdivision is used for the main administrativ...
2        County          7  County is used for smaller administrative divi...
3  Municipality          4  Municipality is used for small administrative ...
4          City          3  City is used for settlements of any size, incl...
5      District          5  District is used for a division of a large cit...
6        Island          6  Island is used for islands and atolls which do...

In [34]:
#Add the area name and type to our main dataframe for the column "area_id":
df4 = pd.merge(df3, areas, how='left', on='area_id')
df4.head()

release_id            release_group  credit_id  group_id  area_id  \
0     2163750                             2205562   1962329    240.0   
1     1846605                             1503027   1713833    240.0   
2     1714060    Beaux Soirs De Paris     1324142   1609358     73.0   
3     2265346                    Le 1     2291833   2042812    240.0   
4     1895266   M2Music HitDisc Vol. 1          1   1751021    222.0   

  release_year  artist_id                           artist_mbid  \
0   2014-01-01  1654312.0  d10d6441-dcc1-4202-93bf-0c0acf72913a   
1   2015-01-01  1112115.0  7b52c77b-1a34-439d-a285-3a7c69cb5b1a   
2   1995-01-01  1122795.0  71b8451c-c10a-400e-9544-101f34ab2522   
3   2018-01-01  1720981.0  a69efb5f-0b28-4328-8ff0-44d8d6f39755   
4   2006-01-01        1.0  89ad4ac3-39f7-470e-963a-56509c546377   

     artist_name_x  start_area1  start_area2      area_name  code_type  
0         Soul Glo       7707.0          NaN    [Worldwide]        NaN  
1      Ben Bennett          NaN          NaN    [Worldwide]        NaN  
2  Soixante Étages          NaN          NaN         France        1.0  
3         TedeuzeM      68613.0          NaN    [Worldwide]        NaN  
4  Various Artists          NaN          NaN  United States        1.0

In [35]:
#Rearranging dataframe columns to have a clearer dataframe:
df4 = df4[['release_id','group_id','release_group','credit_id','area_id','area_name','code_type','release_year','artist_id','artist_mbid','artist_name_x','start_area1','start_area2']]
df4.rename(columns={'area_id':'release_area','area_name':'release_area_name','code_type':'release_code_type','start_area1':'area_id'}, inplace=True)
df4.head()

release_id  group_id            release_group  credit_id  release_area  \
0     2163750   1962329                             2205562         240.0   
1     1846605   1713833                             1503027         240.0   
2     1714060   1609358    Beaux Soirs De Paris     1324142          73.0   
3     2265346   2042812                    Le 1     2291833         240.0   
4     1895266   1751021   M2Music HitDisc Vol. 1          1         222.0   

  release_area_name  release_code_type release_year  artist_id  \
0       [Worldwide]                NaN   2014-01-01  1654312.0   
1       [Worldwide]                NaN   2015-01-01  1112115.0   
2            France                1.0   1995-01-01  1122795.0   
3       [Worldwide]                NaN   2018-01-01  1720981.0   
4     United States                1.0   2006-01-01        1.0   

                            artist_mbid    artist_name_x  area_id  start_area2  
0  d10d6441-dcc1-4202-93bf-0c0acf72913a         Soul Glo   7707.0          NaN  
1  7b52c77b-1a34-439d-a285-3a7c69cb5b1a      Ben Bennett      NaN          NaN  
2  71b8451c-c10a-400e-9544-101f34ab2522  Soixante Étages      NaN          NaN  
3  a69efb5f-0b28-4328-8ff0-44d8d6f39755         TedeuzeM  68613.0          NaN  
4  89ad4ac3-39f7-470e-963a-56509c546377  Various Artists      NaN          NaN

In [36]:
#Add the start area name and type to our main dataframe for the column "area id"(which was "start area 1" before):
df5 = pd.merge(df4, areas, how='left', on='area_id')
df5.head()

release_id  group_id            release_group  credit_id  release_area  \
0     2163750   1962329                             2205562         240.0   
1     1846605   1713833                             1503027         240.0   
2     1714060   1609358    Beaux Soirs De Paris     1324142          73.0   
3     2265346   2042812                    Le 1     2291833         240.0   
4     1895266   1751021   M2Music HitDisc Vol. 1          1         222.0   

  release_area_name  release_code_type release_year  artist_id  \
0       [Worldwide]                NaN   2014-01-01  1654312.0   
1       [Worldwide]                NaN   2015-01-01  1112115.0   
2            France                1.0   1995-01-01  1122795.0   
3       [Worldwide]                NaN   2018-01-01  1720981.0   
4     United States                1.0   2006-01-01        1.0   

                            artist_mbid    artist_name_x  area_id  \
0  d10d6441-dcc1-4202-93bf-0c0acf72913a         Soul Glo   7707.0   
1  7b52c77b-1a34-439d-a285-3a7c69cb5b1a      Ben Bennett      NaN   
2  71b8451c-c10a-400e-9544-101f34ab2522  Soixante Étages      NaN   
3  a69efb5f-0b28-4328-8ff0-44d8d6f39755         TedeuzeM  68613.0   
4  89ad4ac3-39f7-470e-963a-56509c546377  Various Artists      NaN   

   start_area2        area_name  code_type  
0          NaN     Philadelphia        3.0  
1          NaN              NaN        NaN  
2          NaN              NaN        NaN  
3          NaN  Aix-en-Provence        3.0  
4          NaN              NaN        NaN

In [37]:
#Rearranging dataframe columns to have a clearer dataframe:
df5 = df5[['release_id','group_id','release_group','credit_id','release_area','release_area_name','release_code_type','release_year','artist_id','artist_mbid','artist_name_x','area_id','area_name','code_type','start_area2']]
df5.rename(columns={'area_id':'artist_area1','area_name':'artist_area_name1','code_type':'artist_code_type1','start_area2':'area_id'}, inplace=True)
df5.head()

release_id  group_id            release_group  credit_id  release_area  \
0     2163750   1962329                             2205562         240.0   
1     1846605   1713833                             1503027         240.0   
2     1714060   1609358    Beaux Soirs De Paris     1324142          73.0   
3     2265346   2042812                    Le 1     2291833         240.0   
4     1895266   1751021   M2Music HitDisc Vol. 1          1         222.0   

  release_area_name  release_code_type release_year  artist_id  \
0       [Worldwide]                NaN   2014-01-01  1654312.0   
1       [Worldwide]                NaN   2015-01-01  1112115.0   
2            France                1.0   1995-01-01  1122795.0   
3       [Worldwide]                NaN   2018-01-01  1720981.0   
4     United States                1.0   2006-01-01        1.0   

                            artist_mbid    artist_name_x  artist_area1  \
0  d10d6441-dcc1-4202-93bf-0c0acf72913a         Soul Glo        7707.0   
1  7b52c77b-1a34-439d-a285-3a7c69cb5b1a      Ben Bennett           NaN   
2  71b8451c-c10a-400e-9544-101f34ab2522  Soixante Étages           NaN   
3  a69efb5f-0b28-4328-8ff0-44d8d6f39755         TedeuzeM       68613.0   
4  89ad4ac3-39f7-470e-963a-56509c546377  Various Artists           NaN   

  artist_area_name1  artist_code_type1  area_id  
0      Philadelphia                3.0      NaN  
1               NaN                NaN      NaN  
2               NaN                NaN      NaN  
3   Aix-en-Provence                3.0      NaN  
4               NaN                NaN      NaN

In [38]:
#Add the start area 2 name and type to our main dataframe for the column "area id"(which was "start area 2" before):
df6 = pd.merge(df5, areas, how='left', on='area_id')
df6.head()

release_id  group_id            release_group  credit_id  release_area  \
0     2163750   1962329                             2205562         240.0   
1     1846605   1713833                             1503027         240.0   
2     1714060   1609358    Beaux Soirs De Paris     1324142          73.0   
3     2265346   2042812                    Le 1     2291833         240.0   
4     1895266   1751021   M2Music HitDisc Vol. 1          1         222.0   

  release_area_name  release_code_type release_year  artist_id  \
0       [Worldwide]                NaN   2014-01-01  1654312.0   
1       [Worldwide]                NaN   2015-01-01  1112115.0   
2            France                1.0   1995-01-01  1122795.0   
3       [Worldwide]                NaN   2018-01-01  1720981.0   
4     United States                1.0   2006-01-01        1.0   

                            artist_mbid    artist_name_x  artist_area1  \
0  d10d6441-dcc1-4202-93bf-0c0acf72913a         Soul Glo        7707.0   
1  7b52c77b-1a34-439d-a285-3a7c69cb5b1a      Ben Bennett           NaN   
2  71b8451c-c10a-400e-9544-101f34ab2522  Soixante Étages           NaN   
3  a69efb5f-0b28-4328-8ff0-44d8d6f39755         TedeuzeM       68613.0   
4  89ad4ac3-39f7-470e-963a-56509c546377  Various Artists           NaN   

  artist_area_name1  artist_code_type1  area_id area_name  code_type  
0      Philadelphia                3.0      NaN       NaN        NaN  
1               NaN                NaN      NaN       NaN        NaN  
2               NaN                NaN      NaN       NaN        NaN  
3   Aix-en-Provence                3.0      NaN       NaN        NaN  
4               NaN                NaN      NaN       NaN        NaN

In [39]:
#Renaming columns:
df6.rename(columns={'area_id':'artist_area2','area_name':'artist_area_name2','code_type':'artist_code_type2'}, inplace=True)
df6.head()

release_id  group_id            release_group  credit_id  release_area  \
0     2163750   1962329                             2205562         240.0   
1     1846605   1713833                             1503027         240.0   
2     1714060   1609358    Beaux Soirs De Paris     1324142          73.0   
3     2265346   2042812                    Le 1     2291833         240.0   
4     1895266   1751021   M2Music HitDisc Vol. 1          1         222.0   

  release_area_name  release_code_type release_year  artist_id  \
0       [Worldwide]                NaN   2014-01-01  1654312.0   
1       [Worldwide]                NaN   2015-01-01  1112115.0   
2            France                1.0   1995-01-01  1122795.0   
3       [Worldwide]                NaN   2018-01-01  1720981.0   
4     United States                1.0   2006-01-01        1.0   

                            artist_mbid    artist_name_x  artist_area1  \
0  d10d6441-dcc1-4202-93bf-0c0acf72913a         Soul Glo        7707.0   
1  7b52c77b-1a34-439d-a285-3a7c69cb5b1a      Ben Bennett           NaN   
2  71b8451c-c10a-400e-9544-101f34ab2522  Soixante Étages           NaN   
3  a69efb5f-0b28-4328-8ff0-44d8d6f39755         TedeuzeM       68613.0   
4  89ad4ac3-39f7-470e-963a-56509c546377  Various Artists           NaN   

  artist_area_name1  artist_code_type1  artist_area2 artist_area_name2  \
0      Philadelphia                3.0           NaN               NaN   
1               NaN                NaN           NaN               NaN   
2               NaN                NaN           NaN               NaN   
3   Aix-en-Provence                3.0           NaN               NaN   
4               NaN                NaN           NaN               NaN   

   artist_code_type2  
0                NaN  
1                NaN  
2                NaN  
3                NaN  
4                NaN

Now that we have the names of the different areas, let's check what kind of information we have in those columns.

As we said before, we prefer to keep the artist area preferably, as it represents more the real origin of the music.

1) Artist area 1:

In [40]:
df6.artist_area_name1.value_counts()

United States                           273415
United Kingdom                          133067
Japan                                    83908
Germany                                  67463
France                                   45927
Italy                                    27215
Sweden                                   24982
Canada                                   23619
Finland                                  21981
Netherlands                              18101
Australia                                17738
Spain                                    16090
Russia                                   13821
Brazil                                   11142
Belgium                                  10249
Austria                                   8975
Poland                                    8913
Norway                                    8775
South Korea                               8004
Denmark                                   7140
Argentina                                 6576
Greece       

In [41]:
df6.artist_code_type1.value_counts()

1.0    949862
3.0    112208
2.0     24835
4.0      3058
5.0      2429
7.0       254
6.0       114
Name: artist_code_type1, dtype: int64

As we can see, the majority of the artists' start area type we have is related to countries. This would be good for our visualization except for big countries like USA, Canada or Australia, for which we would prefer to retrieve at least the artist's state, to have a clearer view of the music's origin.

Also, we noticed that we have some area names that don't give us much information: "Worldwide", "Europe", "South Australia", etc.

2) Artist area 2:

In [42]:
df6.artist_area_name2.value_counts()

London                                 23087
Los Angeles                            14173
New York                               12434
Chicago                                 8353
Tokyo                                   7784
Paris                                   6395
Brooklyn                                6258
Berlin                                  5941
Philadelphia                            5274
Detroit                                 4659
San Francisco                           4574
Toronto                                 4068
Boston                                  3959
Seattle                                 3938
Seoul                                   3800
Stockholm                               3448
Melbourne                               3308
Hamburg                                 3259
United Kingdom                          3170
Montreal                                3106
Wien                                    2827
Sydney                                  2798
Buenos Air

In [43]:
df6.artist_code_type2.value_counts()

3.0    481180
2.0     61532
1.0     31001
5.0     25596
4.0     20562
7.0      2487
6.0       556
Name: artist_code_type2, dtype: int64

It looks like this second column could be giving us more detailed information about the artist's origin (only 31K rows have countries). 

We will keep the detail in "artist_area_name2" and "artist_code_type2" as the origin for the rows who have that information, and fill the other rows with "artist_area_name1" and "artist_code_type1"

In [44]:
#First, we rename our columns:
df6.rename(columns={'artist_area_name2':'origin_name','artist_code_type2':'origin_code'}, inplace=True)
df6.head()

release_id  group_id            release_group  credit_id  release_area  \
0     2163750   1962329                             2205562         240.0   
1     1846605   1713833                             1503027         240.0   
2     1714060   1609358    Beaux Soirs De Paris     1324142          73.0   
3     2265346   2042812                    Le 1     2291833         240.0   
4     1895266   1751021   M2Music HitDisc Vol. 1          1         222.0   

  release_area_name  release_code_type release_year  artist_id  \
0       [Worldwide]                NaN   2014-01-01  1654312.0   
1       [Worldwide]                NaN   2015-01-01  1112115.0   
2            France                1.0   1995-01-01  1122795.0   
3       [Worldwide]                NaN   2018-01-01  1720981.0   
4     United States                1.0   2006-01-01        1.0   

                            artist_mbid    artist_name_x  artist_area1  \
0  d10d6441-dcc1-4202-93bf-0c0acf72913a         Soul Glo        7707.0   
1  7b52c77b-1a34-439d-a285-3a7c69cb5b1a      Ben Bennett           NaN   
2  71b8451c-c10a-400e-9544-101f34ab2522  Soixante Étages           NaN   
3  a69efb5f-0b28-4328-8ff0-44d8d6f39755         TedeuzeM       68613.0   
4  89ad4ac3-39f7-470e-963a-56509c546377  Various Artists           NaN   

  artist_area_name1  artist_code_type1  artist_area2 origin_name  origin_code  
0      Philadelphia                3.0           NaN         NaN          NaN  
1               NaN                NaN           NaN         NaN          NaN  
2               NaN                NaN           NaN         NaN          NaN  
3   Aix-en-Provence                3.0           NaN         NaN          NaN  
4               NaN                NaN           NaN         NaN          NaN

In [45]:
#And now we can fill the NaNs with the values in "artist_area_name1" and "artist_code_type1":
df6['origin_name'].fillna(df6['artist_area_name1'], inplace=True)
df6['origin_code'].fillna(df6['artist_code_type1'], inplace=True)
#We can also delete some columns that we don't need anymore:
df6.drop(labels=['artist_area1','artist_area_name1','artist_code_type1','artist_area2'], axis=1, inplace=True)

In [46]:
#Now, let's see what information we have for these new columns:
df6.origin_name.value_counts()

United States                       81824
United Kingdom                      52861
Japan                               42326
Germany                             34085
London                              26075
France                              26057
Los Angeles                         16492
Sweden                              15460
Italy                               15210
New York                            14259
Finland                             13767
Netherlands                         10886
Chicago                              9463
Spain                                9225
Canada                               8819
Australia                            8720
Russia                               8592
Tokyo                                8367
Berlin                               7558
Paris                                7546
Brooklyn                             7031
Poland                               6282
Philadelphia                         5823
Seattle                           

In [47]:
df6.origin_code.value_counts()

3.0    544417
1.0    433886
2.0     74659
5.0     26638
4.0     22369
7.0      2623
6.0       612
Name: origin_code, dtype: int64

In [48]:
#Now, let's see how many empty rows we have:
df6.isnull().sum(axis=0)

release_id                0
group_id                  0
release_group             4
credit_id                 0
release_area              0
release_area_name         0
release_code_type    241017
release_year              0
artist_id               151
artist_mbid             151
artist_name_x           155
origin_name          392302
origin_code          394410
dtype: int64

As we mentioned earlier, we want our visualization to be as detailed as possible, especially where the country of origin is very large, or has a big volume of releases.

What we will do is extract from our dataframe all the rows for which the "origin area" is either empty or represents a large country or a large volume.

Then, we will group by artist and try to find their origin in other sources of information.

In [49]:
#We create a new dataframe containing the target rows:

target = ['United States', 'United Kingdom', 'Japan', 'Germany', 'France', 'Canada', 'Australia', 'Russia',
          '[Worldwide]', 'Europe']
a = df6.loc[df6['origin_name'].isnull()]
b = df6[df6['origin_name'].isin(target)]

unknown_area = pd.concat([a, b], ignore_index=True)
unknown_area.origin_name.value_counts()

United States     81824
United Kingdom    52861
Japan             42326
Germany           34085
France            26057
Canada             8819
Australia          8720
Russia             8592
[Worldwide]        1822
Europe              300
Name: origin_name, dtype: int64

In [50]:
#How many unique artists are there with no area info?
unknown_area['artist_id'].nunique()

215736

In [51]:
#And how many releases are affected?
unknown_area['release_id'].nunique()

657708

So, according to the above line, we have 215.736 artists with unknown or vague origin. Let's have a closer look:

In [52]:
unknown_artist = unknown_area.groupby('artist_name_x').count().sort_values('release_id',ascending=False)
unknown_artist.head(1000)

release_id  group_id  \
artist_name_x                                                              
Various Artists                                         134857    134857   
[unknown]                                                 1363      1363   
Glee Cast                                                  474       474   
Duke Ellington & His Orchestra                             288       288   
[language instruction]                                     278       278   
Vitamin String Quartet                                     252       252   
Senmuth                                                    249       249   
Die drei ???                                               244       244   
モーニング娘。                                                    219       219   
Stefan Wolf                                                211       211   
101 Strings                                                187       187   
THE ALFEE                                                  186       186   
Dwelling of Duels                                          180       180   
[nature sounds]                                            170       170   
Enid Blyton                                                165       165   
Kevin Drumm                                                142       142   
TAMUSIC                                                    141       141   
初音ミク                                                       141       141   
Benny Goodman and His Orchestra                            133       133   
Aidan Baker                                                132       132   
Michel Sardou                                              126       126   
Falcom Sound Team jdk                                      126       126   
[Disney]                                                   123       123   
Peerless Orchestra                                         122       122   
Edison Concert Band                                        115       115   
Dan Gibson                                                 114       114   
コナミ矩形波倶楽部                                                  112       112   
[dialogue]                                                 112       112   
ASC                                                        111       111   
桜庭統                                                        111       111   
Bibi & Tina                                                109       109   
Eddy Mitchell                                              107       107   
Art Blakey & The Jazz Messengers                           105       105   
Аквариум                                                   104       104   
ZUNTATA                                                    103       103   
Blank & Jones                                              103       103   
Above & Beyond                                             101       101   
ALI PROJECT                                                101       101   
B’z                                                        100       100   
HasenChat Music                                            100       100   
Every Little Thing                                          99        99   
How Did This Get Made?                                      98        98   
℃‐ute                                                       98        98   
Loudness                                                    97        97   
Edward M. Favor                                             97        97   
Klaus Wiese                                                 97        97   
Berryz工房                                                    96        96   
KK Null                                                     96        96   
SoLaRiS                                                     95        95   
Tim Pritlove                                                95        95   
Samuel Sagan                                                95        95   
Chicago Symphony Orchest

In [53]:
#From what we can see above, the category "Various Artists" has many releases assigned:
df6[df6['artist_name_x']=='Various Artists']

release_id  group_id  \
4           1895266   1751021   
26           356044     14028   
41          1623578   1539062   
44           475440    785494   
45            62055     28102   
46          1053661   1078102   
47            62061    147591   
48          1447852    147591   
49          1012140    955241   
50          2319247   2084339   
51          2327624   2090989   
53           725914    981951   
69           686550    952517   
70          1630852   1544917   
83          1572461   1498671   
193          510871    815185   
194         2241261   2024009   
195         1582410   1506660   
196         1766351   1651172   
208         1350888   1316456   
209          178590    363395   
211          402912    725927   
212         1766782   1651511   
214          404062    726818   
215          412730    733697   
216          117141    489665   
217         1563701   1491838   
218         1563690   1491828   
219          127131    497868   
220          597713    230258   
221         1489657   1430380   
222           27281     92007   
223          804099   1044425   
224          616073    897598   
225          175209    535717   
226          558349    853335   
227          718542    976639   
228          170562    532005   
231         1079850   1099410   
234          192133    257320   
236         1859994   1724263   
244          643165    918166   
245          266373    613611   
246          643163    918163   
247         2158299   1957818   
261         2142036   1944551   
266         2136733   1940281   
276         2154803   1954915   
298          695486    959137   
299          815395   1053025   
301          494614    404672   
302          494615    404672   
527         1696475   1595501   
532         1244270   1231951   
546         2258755   2037508   
550         1921996   1771758   
559         1666943   1572776   
560         1733488   1624804   
561         1851437   1717709   
585         1665198   1526696   
590         1885508   1743604   
602         1715569   1610630   
603         1741986   1631577   
604         1886150   1744091   
605         1964229   1804542   
606         1987806   1822815   
607         1912195   1764056   
608         2013746   1843376   
610         1341778   1292582   
611         1320062   1292582   
623         1572647   1498815   
637         2119677   1926837   
639         2095250   1907984   
686         1871830   1733169   
707         1667675   1573395   
713         2277681   2052377   
716         2140880   1943579   
729         1636380   1549049   
743         1680869   1583498   
744         1179685   1179216   
807         2259869   2038439   
812         1926616   1775441   
813         1920710   1770681   
821         1840768   1709371   
836         2294251   2065088   
837         1787503   1668274   
838         1772117   1655788   
839         1443992   1389614   
840         1672256   1577046   
841         1984321   1820177   
842         1749363   1637611   
844         2085678   1900344   
851         1063584   1085955   
860         1703879   1601355   
864         2273687   2049193   
865         2268940   2045532   
899         1858097   1722728   
900         2378142   2132268   
908         1206048   1200392   
962           62183    409659   
1021         803237   1043713   
1022        1608677   1043713   
1026          42723    360786   
1027         149452    515813   
1067        1280010   1240524   
1119         555669    851339   
1135         920178    303155   
1136        1224130   1215417   
1137        2255960   2035236   
1138        2256493   2035663   
1139        2256506   2035673   
1140        2256518   2035681   
1141         370569    699384   
1142        1605034   1524122   
1143        2322750   2087068   
1144         128603    499316   
1167         465018    590695   
1168        2135911   1939634   
1169        1032069    637798   
1170         952153    373387   
1171         100

If we look in detail into these releases, we can see that most of them are music compilations (hence the generic category "Various Artists"). As they are music compilations, that means that the tracks included were originally released before by their genuine author, so we shouldn't take them into account (to avoid duplicates). Also, as we don't have an artist name for them, it will be impossible to retrieve the origin.

We will delete those rows from our datasets.

Let's analyze more in detail who are the rest of artists that have many releases, and decide what to do with them.

In [54]:
#Unknown artist:
df6[df6['artist_name_x']=='[unknown]']

release_id  group_id  \
7287         546135    843736   
8817         557295    852580   
9663        1232110   1222115   
9664         665743    936259   
9817        1235032   1224582   
9918         638247    914460   
10852       1208592   1202487   
11319        686485    952465   
11705       1247647   1234682   
16973       1015709    616974   
24882        652504    925618   
25162       1120161   1131958   
25223        507071    812060   
25406        718072    976309   
27709       1076239   1096301   
27736       1076251   1096313   
28521       1803794   1680861   
28648       2251694   2032015   
29907        802135   1042815   
32043       1770134   1654219   
32064       1076245   1096307   
32072        306795    505882   
32288        834578    343638   
32303        441061    757278   
33466       1621932   1537731   
33479        295640    636878   
38222       1141187   1149295   
38412        171852     97395   
38565       1406338    166773   
41740       1899225   1753979   
42342        723303    980024   
44820        170600    532082   
50770        385441    711393   
50857        385379    711356   
52826       1621937   1537734   
55628        790966   1034124   
55629       1279385   1260311   
58412       2144016   1946077   
61001       2266934   2043997   
63270        307361     76734   
63609       1606327   1525151   
64228        611031    893833   
64476        689638      7769   
64533        745216    997430   
68738        386900    712566   
68739        386938    712606   
70650       1601721   1521568   
71897        323081    661055   
76753       1421635   1372120   
77706        975819    461533   
77707        675700    944055   
77709       1830415   1701189   
77722       1739170    944055   
77727       1738478   1628717   
82614        386921    712589   
84897        386885    712490   
85039       1958720   1800489   
85040       1958725   1800492   
88623       1733372   1624705   
88625       1567999   1495260   
88976        385389    711361   
89143       1838622   1707684   
92442        458587    771506   
93008       1432362   1380718   
94321        386894    712560   
94583        386954    712622   
96589        620485    900996   
96590        620489    901000   
96591        620490    901001   
96592        620491    901002   
96593        620492    901003   
96993        407491    729517   
96994        407332    729380   
96995        407498    729524   
96996        407340    729386   
97892        534901    834615   
98407        352585    684987   
99831        802138   1042818   
101418       507473    812410   
101734      2117215    649710   
106387      1559312   1488484   
107203       386767    712486   
107430      1590042   1512512   
108804      1456055   1399200   
109961       385409    711372   
114651      2324415   2088450   
115518       414657    735229   
115519       567666    860313   
116418       820311   1056828   
116492      1621939   1537736   
116730       474401    735836   
116987      1911548   1763576   
117765       386946    712614   
118259       386823    712511   
119435      2028978   1855210   
124886      1700686   1598855   
124968       578111    868183   
128463      1803383   1680528   
130317       892915    166244   
131435       746867    998816   
132336      2134733   1938703   
135209       284633    628307   
137457      1903352   1757196   
137838      1903337   1757181   
139822       598480    883678   
140364       965380    422006   
141172      1105183   1119601   
142649       625578    904811   
142690      1978769   1815786   
143978       386859    712527   
145074      1837100   1706474   
145821      2158522   1958007   
145840       155061    520242   
147040      1504867   1444422   
147767       386951    712619   
151189       317401    656383   
152181      1837414   1706707   
153648      2207655   1997677   
157000       386805    712503   
159464       386918    712586   
166291      1570

The category "unknown" seems to contain music compilations too.

In [55]:
#"Language instruction" artist:
df6[df6['artist_name_x']=='[language instruction]']

release_id  group_id  \
11186        821781   1057780   
11187        822699   1058470   
30861        536732    836303   
51254       1921485   1771345   
51811       1920797   1770754   
73778       2107126   1916950   
78295        685879    731447   
81802       1381788   1341586   
82122       1921562   1771391   
100674      1921270   1771164   
102318       630154    908206   
102319       630138    908192   
102320      1228950   1219452   
104311      1921572   1771400   
104312      1921489   1771348   
112036      1921584   1771412   
112111      1920817   1770774   
112230      1920800   1770757   
112231      1920798   1770755   
112232      1920805   1770762   
112233      1920475   1770482   
112234      1921491   1771350   
112235      1921552   1771383   
112236      1920804   1770761   
112238      1920818   1770775   
112239      1920814   1770771   
112240      1920802   1770759   
112241      1920480   1770485   
112242      1920451   1770461   
112243      1920481   1770486   
112244      1920469   1770476   
112245      1920811   1770768   
112246      1920497   1770501   
112248      1920786   1770745   
112249      1921267   1771161   
125331      2014765   1844091   
125332      2014773   1844098   
125333       475724    785748   
125334       478425    787954   
136211       424205    743286   
147904       500267    806432   
147905      1666738   1572611   
151743      1856198   1721247   
153551      1921581   1771409   
176673       361228    691457   
184977      1921576   1771404   
231742      1920792   1770750   
237484      1921582   1771410   
248533      1920472   1770479   
255066      1920815   1770772   
278640      1921543   1771375   
278641      1920824   1770781   
306608       677095    945175   
310424       798635   1040421   
312230      1920810   1770767   
320683      1920794   1770751   
342732       825118   1060439   
342733      1107637   1121619   
342736      1169168   1170844   
350010       376354    704217   
350011       403893    726680   
350936       853354   1028371   
352092      2033014   1858490   
352093      2033035   1858506   
356198      1924499   1773666   
356199      2024784   1773666   
358091      1921548   1771380   
361594       688016    953472   
376411      1099755   1111419   
376415      1378040   1338477   
376416       450585    765098   
376523      1745252   1634291   
376524      1739692   1629724   
376525      1974677   1812634   
403222      1920453   1770463   
403494      1920822   1770779   
403621      1921561   1771390   
406104       402551    725573   
407023      1920788   1770746   
409942      1921550   1771381   
414122       786312   1030424   
416331      1236487   1225772   
435003      1236592   1225856   
435092       283506    627448   
438083       183212    542674   
438143       767205   1015266   
438144       767756   1015698   
438145       767771   1015709   
438146       767782   1015717   
438147       767793   1015720   
438281       909943    766770   
456947       502359    808207   
456948       557483    852724   
457862       546316    843845   
457863       547435    844694   
457864       547448    844707   
457865       719321    977159   
457866       719327    977171   
457911       759415   1009334   
457917       630672    908612   
460727      1920471   1770478   
465648      1920470   1770477   
484475      1817620   1691430   
484476      1818484   1692086   
484477      1818330   1691962   
484496      1921564   1771392   
506323      1921542   1771374   
525855      1724248   1617519   
530336      1920808   1770765   
531631      1106145   1120387   
536115      1921540   1771372   
536868      1920486   1770491   
538554       519749    251752   
576368       259244    607521   
583023       409803    731465   
587274      1920442   1770455   
588550      1921541   1771373   
591523      1921553   1771384   
594996       436837    753713   
595129       858858    862256   
595145       687

As its name suggests, these releases are language courses recorded, so they are not music and they are out of our scope too.

The same would apply to the categories [nature sounds], [dialogue] or [christmas music].

We can now delete from our dataframes all these cathegories, and see what we have left.

In [56]:
#In our main dataframe:
df7 = df6.replace(['[nature sounds]','[dialogue]','[christmas music]', 'Various Artists','[unknown]','[language instruction]'], pd.np.nan).dropna(axis=0, subset=['artist_name_x'])

In [57]:
#In our unknown_area dataframe:
unknown_area = unknown_area.replace(['[nature sounds]','[dialogue]','[christmas music]', 'Various Artists','[unknown]','[language instruction]'], pd.np.nan).dropna(axis=0, subset=['artist_name_x'])

In [58]:
#So how many artists do we have to identify their origin for?
unknown_area['artist_id'].nunique()

215727

In [59]:
#We export the unique artists to a dataframe in order to retrieve the information later:
unknown_artist = unknown_area.drop_duplicates(subset='artist_id')
unknown_artist.drop(labels=['release_id','release_group','credit_id','release_area','release_area_name','release_code_type', 'release_year'], axis=1,inplace=True)
unknown_artist.head()

/home/ainhoa/anaconda3/envs/kschool/lib/python3.7/site-packages/pandas/core/frame.py:3940: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  errors=errors)


group_id  artist_id                           artist_mbid    artist_name_x  \
0   1713833  1112115.0  7b52c77b-1a34-439d-a285-3a7c69cb5b1a      Ben Bennett   
1   1609358  1122795.0  71b8451c-c10a-400e-9544-101f34ab2522  Soixante Étages   
3   1435283  1154943.0  2b0e7ee2-a1d0-45d9-9291-2d269bea9160          三田村管打団?   
6   1596377  1304306.0  27f68a42-6f60-4628-9a01-47a62d7f7cdc      Gus Rachels   
8   1438559  1170204.0  595b6f86-d893-4cee-8df2-104920ea2a37              SDR   

  origin_name  origin_code  
0         NaN          NaN  
1         NaN          NaN  
3         NaN          NaN  
6         NaN          NaN  
8         NaN          NaN

# Data from the 1 million songs dataset

Between 2011 and 2012, there was a Music Information Retrieval challenge called "Million Song Dataset". The majority of the data contained was provided by The Echo Nest (today known as Spotify).

At the bottom of the following website, there are links to download the Dataset:

https://labrosa.ee.columbia.edu/millionsong/pages/getting-dataset

As we won't use the whole dataset (just some of the tables), you don't need to download them: they will be attached in the repo.

In [60]:
artists_locations = pd.read_csv('1M_songs/artist_location.csv',sep='<SEP>', header=None, engine='python')

In [61]:
artists_locations.columns = ['artist_id','lat','long','artist_name','location_name']
artists_locations.head()

artist_id       lat      long           artist_name  \
0  ARZGXZG1187B9B56B6 -16.96595 -61.14804          Endless Blue   
1  AR8K6F31187B99C2BC  46.44231 -93.36586               Go Fish   
2  ARHJJ771187FB5B581  51.59678  -0.33556  Screaming Lord Sutch   
3  ARJ8YLL1187FB3CA93  40.69626 -73.83301          Morton Gould   
4  ARYBAGV11ECC836DAC  43.58828 -79.64372        Crash Parallel   

                location_name  
0                  Santa Cruz  
1             Twin Cities, MN  
2  Harrow, Middlesex, England  
3           Richmond Hill, NY  
4                 Mississauga

In [62]:
len(artists_locations)

13850

In [63]:
tracks_metadata = pd.read_csv('1M_songs/track_metadata.csv',sep=',', header=0, engine='python', usecols=['artist_id','artist_mbid'])
tracks_metadata.head()

artist_id                           artist_mbid
0  ARYZTJS1187B98C555  357ff05d-848a-44cf-b608-cb34b5701ae5
1  ARMVN3U1187FB3A1EB  8d7ef530-a6fd-4f8f-b2e2-74aec765e0f9
2  ARGEKB01187FB50750  3d403d44-36ce-465c-ad43-ae877e65adc4
3  ARNWYLR1187B9B2F9C  12be7648-7094-495f-90e6-df4189d68615
4  AREQDTE1269FB37231                                   NaN

In [64]:
tracks_metadata.dropna(subset=['artist_mbid'],axis=0, inplace=True)
a = pd.merge(artists_locations,tracks_metadata,how='left',on='artist_id')
a.dropna(subset=['artist_mbid'],axis=0, inplace=True)
a.head()

artist_id       lat      long   artist_name    location_name  \
0  ARZGXZG1187B9B56B6 -16.96595 -61.14804  Endless Blue       Santa Cruz   
1  ARZGXZG1187B9B56B6 -16.96595 -61.14804  Endless Blue       Santa Cruz   
2  AR8K6F31187B99C2BC  46.44231 -93.36586       Go Fish  Twin Cities, MN   
3  AR8K6F31187B99C2BC  46.44231 -93.36586       Go Fish  Twin Cities, MN   
4  AR8K6F31187B99C2BC  46.44231 -93.36586       Go Fish  Twin Cities, MN   

                            artist_mbid  
0  0bd9755c-c86d-431c-bc28-ef908b8a9821  
1  0bd9755c-c86d-431c-bc28-ef908b8a9821  
2  d4620364-82ec-4c34-9265-a2b72dfa8e3e  
3  d4620364-82ec-4c34-9265-a2b72dfa8e3e  
4  d4620364-82ec-4c34-9265-a2b72dfa8e3e

In [65]:
a.drop_duplicates(subset='artist_id', inplace=True)
a.drop(labels=['artist_id','lat','long'], axis=1, inplace=True)
a.head()

artist_name               location_name  \
0           Endless Blue                  Santa Cruz   
2                Go Fish             Twin Cities, MN   
33  Screaming Lord Sutch  Harrow, Middlesex, England   
64          Morton Gould           Richmond Hill, NY   
78        Crash Parallel                 Mississauga   

                             artist_mbid  
0   0bd9755c-c86d-431c-bc28-ef908b8a9821  
2   d4620364-82ec-4c34-9265-a2b72dfa8e3e  
33  e1079a78-75d4-4a1a-aef1-0be051386598  
64  4db4e744-3007-4386-b87d-9653acfe0464  
78  b0d85cf7-b73b-4a5d-bf31-a82493c3a8a8

Can we retrieve some of our "unknown_artist" locations with this dataframe?

In [66]:
b = pd.merge(unknown_artist,a,how='left',on='artist_mbid')
b.notnull().sum(axis=0)

group_id         215728
artist_id        215728
artist_mbid      215728
artist_name_x    215728
origin_name       75476
origin_code       75218
artist_name        3487
location_name      3486
dtype: int64

If we look at the field "location name", we can see that we have just retrieved the location for 3486 artists with the Million Song Dataset help.

In [67]:
#What kind on information is contained in that field?
b.location_name.value_counts()

California - LA                                               130
NY - New York City                                            113
California                                                     67
California - SF                                                66
New York, NY                                                   62
Texas                                                          56
London, England                                                47
Los Angeles, CA                                                46
GERMANY                                                        42
Great Britain / UK                                             42
Tennessee                                                      39
United States                                                  39
Chicago, IL                                                    36
New Jersey                                                     36
CANADA - Ontario                                               34
Washington

It seems pretty detailed so we can keep it for the rest of our project. Let's put that information in the column "origin name" and delete the useless columns:

In [68]:
b[['location_name']].replace(np.nan, 0, inplace=True)

/home/ainhoa/anaconda3/envs/kschool/lib/python3.7/site-packages/pandas/core/frame.py:4042: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  method=method)


In [69]:
b.replace(np.nan, 0, inplace=True) #by doing this the following loop goes much faster
for i in tqdm(range(len(b))):
    if b['location_name'][i] != 0:
        b['origin_name'][i] = b['location_name'][i]
    else:
        pass

  0%|          | 0/215728 [00:00<?, ?it/s]/home/ainhoa/anaconda3/envs/kschool/lib/python3.7/site-packages/ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  after removing the cwd from sys.path.
100%|██████████| 215728/215728 [00:57<00:00, 3771.93it/s] 


In [70]:
b.replace(0,pd.np.nan, inplace=True)
b.drop(labels=['artist_name','location_name'],axis=1, inplace=True)
b.head()

group_id  artist_id                           artist_mbid    artist_name_x  \
0   1713833  1112115.0  7b52c77b-1a34-439d-a285-3a7c69cb5b1a      Ben Bennett   
1   1609358  1122795.0  71b8451c-c10a-400e-9544-101f34ab2522  Soixante Étages   
2   1435283  1154943.0  2b0e7ee2-a1d0-45d9-9291-2d269bea9160          三田村管打団?   
3   1596377  1304306.0  27f68a42-6f60-4628-9a01-47a62d7f7cdc      Gus Rachels   
4   1438559  1170204.0  595b6f86-d893-4cee-8df2-104920ea2a37              SDR   

  origin_name  origin_code  
0         NaN          NaN  
1         NaN          NaN  
2         NaN          NaN  
3         NaN          NaN  
4         NaN          NaN

In [71]:
b.head(1000)

group_id  artist_id                           artist_mbid  \
0     1713833  1112115.0  7b52c77b-1a34-439d-a285-3a7c69cb5b1a   
1     1609358  1122795.0  71b8451c-c10a-400e-9544-101f34ab2522   
2     1435283  1154943.0  2b0e7ee2-a1d0-45d9-9291-2d269bea9160   
3     1596377  1304306.0  27f68a42-6f60-4628-9a01-47a62d7f7cdc   
4     1438559  1170204.0  595b6f86-d893-4cee-8df2-104920ea2a37   
5     1334751   689714.0  66dfce65-8775-45be-9752-2e0ca77aad13   
6     1205176   607730.0  29cd0eb8-b431-4b63-a536-8100c74f0ee0   
7      765607   504980.0  ee1e8412-a686-4e70-a44b-09ba68c2a5ca   
8      683689   448248.0  c83caa4b-aa3c-47db-9a61-3be56942d980   
9      747414   511943.0  81427c2e-7c74-42bc-bcbf-756536e52c30   
10     804059   173266.0  d2e95676-bc19-479a-affe-8af8588fafb8   
11     499471   347836.0  787f5d19-4870-4dfa-999f-385c7bfadb33   
12     730890   181546.0  ae35afc4-8afd-4eec-8406-73a12f5bf009   
13     732624   537938.0  3b901075-06d8-4088-bf6e-6afef888bd54   
14     919379   648106.0  0d81d2d1-ce8c-415c-b529-e097293fba0f   
15     976261   158585.0  65bc10c5-4fcd-48f3-9fb1-97c14c466f3f   
16    1890444  1586509.0  1af91d93-ae49-4859-b606-b6c8a64c5800   
17     879120   647782.0  87051ee0-a457-4706-8915-0624067450b6   
18    1295898  1038185.0  8f9f00c6-43a1-40d8-b3a5-ecc16e298925   
19    2074427   672213.0  113f6a38-ba7d-4a88-bd7a-afb57d91ad06   
20    1376977  1115561.0  58bcb90a-d731-433b-a552-879ab6a9ea02   
21     153427    56198.0  52524166-5d5c-47e1-902d-cef97f1f964e   
22     651172   193339.0  6b6ec3d7-642a-4ede-a800-17ae800625fe   
23    1803327   308435.0  b709792e-6738-4941-90f7-6339cc736d61   
24     954830   710725.0  1e6e3fef-ffd6-4aff-992d-626231289cc3   
25     369594   259483.0  cde67656-bb60-405b-9b1b-78795eeda2f6   
26     595154   372115.0  65fd9bcf-aae7-470a-a5e1-cd7c6a3c6e0d   
27     579876   413857.0  50b2cdd6-5c14-4085-b7bf-be10d4b24c89   
28     594376   365674.0  65193458-d980-4416-853e-68d611a90ad8   
29     642715   463363.0  95c161dc-bdcc-4b63-9c9f-219ae5b8bb46   
30     876857   646325.0  b2ee49b6-7bdd-4934-a10b-264a433d4923   
31    1175110   905043.0  ebfbb569-94dd-4187-aa10-c43bc025733b   
32    1349550   372766.0  a90c5136-3203-4395-a136-e62aa2c11596   
33    1347930   492881.0  b677773b-ef83-450a-b3e1-a40458df9877   
34    1765393   906563.0  5cb7f216-8721-4e0f-a894-949fbc977bbb   
35    1313036  1054500.0  7e311d6a-5249-427a-b2b6-74b4429d8187   
36    1618812  1326662.0  6ea9136c-eff1-4bc0-b465-91071cba6612   
37    1901639  1598943.0  aa50bf13-4be7-4f88-87f9-aef90c7c53ed   
38     809486   597896.0  3f335d09-b12e-46ef-8c82-6eaf7b14b002   
39     570339   406840.0  7f0a3961-6a9f-4cdc-aa87-075eab8d238a   
40     731998   537499.0  628b0adf-6501-48e3-85b5-e88fa3df816a   
41    1920244   574750.0  ad58cbc0-d681-44dd-94fd-81c02e00f90e   
42    1898469   711084.0  6922d0f6-b3f7-4ad9-9749-3c09d7b0a2a1   
43    1264908   211937.0  34bd1af7-1a96-4007-aad6-57fe385d0d9d   
44    1379523   354436.0  95fe1094-69c2-4764-b4ea-27cac80ec192   
45    2077602   360314.0  2d0e1d0a-efaf-4abd-a865-9255557eec94   
46    1010065   757786.0  be96caa2-5cc6-4b46-b801-4824b8d03077   
47     179786   134469.0  bc9dfb59-e7f9-467b-a99a-187f5010e8c3   
48     574398   409854.0  ab7cf0c4-ad3d-4935-adf3-374e106d0057   
49    1522144   450126.0  7cb93905-96cc-4acf-8c95-301f090b2c13   
50    1180217   911502.0  c58eaecd-f990-4462-9bec-fe32ab7ca4e2   
51    1765491   726900.0  14bd08f4-9b4b-4535-b7b3-9da685455d6d   
52     622275   222448.0  16e1f24e-2950-4d52-bfe1-083def5c4d45   
53    1023593   172825.0  c420bee1-c40c-4149-b326-750e38093880   
54    1395065   406996.0  c546182f-6f5c-4977-8186-77b3b7d4b80e   
55    1433903  1154596.0  22047317-b586-4807-a3a7-c8e9d4adffc1   
56    1924432  1606612.0  0abf14d0-fa69-4554-9ae7-14b4539177d3   
57    1810861  1513975.0  1495e7b8-8e9e-4760-b3d5-c9c1dd491c80   
58    1850690  1128019.0  1458d580-c7cf-46a4-a98e-ec2c0cef5e58   
59    1314812  1056324.0  f898d4e9-4401-4151-

In [72]:
b.isnull().sum(axis=0)

group_id              0
artist_id             0
artist_mbid           0
artist_name_x         0
origin_name      139015
origin_code      140510
dtype: int64

In [73]:
len(b)

215728

In [74]:
df7.head()

release_id  group_id           release_group  credit_id  release_area  \
0     2163750   1962329                            2205562         240.0   
1     1846605   1713833                            1503027         240.0   
2     1714060   1609358   Beaux Soirs De Paris     1324142          73.0   
3     2265346   2042812                   Le 1     2291833         240.0   
5     1772538   1656147            devil jokes     1653884         240.0   

  release_area_name  release_code_type release_year  artist_id  \
0       [Worldwide]                NaN   2014-01-01  1654312.0   
1       [Worldwide]                NaN   2015-01-01  1112115.0   
2            France                1.0   1995-01-01  1122795.0   
3       [Worldwide]                NaN   2018-01-01  1720981.0   
5       [Worldwide]                NaN   2016-01-01  1363025.0   

                            artist_mbid    artist_name_x      origin_name  \
0  d10d6441-dcc1-4202-93bf-0c0acf72913a         Soul Glo     Philadelphia   
1  7b52c77b-1a34-439d-a285-3a7c69cb5b1a      Ben Bennett              NaN   
2  71b8451c-c10a-400e-9544-101f34ab2522  Soixante Étages              NaN   
3  a69efb5f-0b28-4328-8ff0-44d8d6f39755         TedeuzeM  Aix-en-Provence   
5  c941ad72-8b13-4940-8d99-0ed9becad2d7            yzome          Seattle   

   origin_code  
0          3.0  
1          NaN  
2          NaN  
3          3.0  
5          3.0

In [95]:
#We can now merge our dataframe with the information we retrieved from 1 Million Songs Dataset:
df8 = pd.merge(df7, b, how='left', on='artist_id')
df8.head()

release_id  group_id_x           release_group  credit_id  release_area  \
0     2163750     1962329                            2205562         240.0   
1     1846605     1713833                            1503027         240.0   
2     1714060     1609358   Beaux Soirs De Paris     1324142          73.0   
3     2265346     2042812                   Le 1     2291833         240.0   
4     1772538     1656147            devil jokes     1653884         240.0   

  release_area_name  release_code_type release_year  artist_id  \
0       [Worldwide]                NaN   2014-01-01  1654312.0   
1       [Worldwide]                NaN   2015-01-01  1112115.0   
2            France                1.0   1995-01-01  1122795.0   
3       [Worldwide]                NaN   2018-01-01  1720981.0   
4       [Worldwide]                NaN   2016-01-01  1363025.0   

                          artist_mbid_x  artist_name_x_x    origin_name_x  \
0  d10d6441-dcc1-4202-93bf-0c0acf72913a         Soul Glo     Philadelphia   
1  7b52c77b-1a34-439d-a285-3a7c69cb5b1a      Ben Bennett              NaN   
2  71b8451c-c10a-400e-9544-101f34ab2522  Soixante Étages              NaN   
3  a69efb5f-0b28-4328-8ff0-44d8d6f39755         TedeuzeM  Aix-en-Provence   
4  c941ad72-8b13-4940-8d99-0ed9becad2d7            yzome          Seattle   

   origin_code_x  group_id_y                         artist_mbid_y  \
0            3.0         NaN                                   NaN   
1            NaN   1713833.0  7b52c77b-1a34-439d-a285-3a7c69cb5b1a   
2            NaN   1609358.0  71b8451c-c10a-400e-9544-101f34ab2522   
3            3.0         NaN                                   NaN   
4            3.0         NaN                                   NaN   

   artist_name_x_y origin_name_y  origin_code_y  
0              NaN           NaN            NaN  
1      Ben Bennett           NaN            NaN  
2  Soixante Étages           NaN            NaN  
3              NaN           NaN            NaN  
4              NaN           NaN            NaN

In [96]:
#Now, fill the values in the column "origin name x" and "origin code x" with the ones from b:
df8['origin_name_x'].fillna(df8['origin_name_y'], inplace=True)
df8['origin_code_x'].fillna(df8['origin_code_y'], inplace=True)
#We can also delete the extra columns:
df8.drop(labels=['artist_mbid_y','artist_name_x_y','origin_name_y','origin_code_y'], axis=1, inplace=True)
#And change the name of some of the remaining columns:
df8.rename(columns={'artist_mbid_x':'artist_mbid','artist_name_x_x':'artist_name','origin_name_x':'origin_name','origin_code_x':'origin_code'}, inplace=True)
df8.head()

release_id  group_id_x           release_group  credit_id  release_area  \
0     2163750     1962329                            2205562         240.0   
1     1846605     1713833                            1503027         240.0   
2     1714060     1609358   Beaux Soirs De Paris     1324142          73.0   
3     2265346     2042812                   Le 1     2291833         240.0   
4     1772538     1656147            devil jokes     1653884         240.0   

  release_area_name  release_code_type release_year  artist_id  \
0       [Worldwide]                NaN   2014-01-01  1654312.0   
1       [Worldwide]                NaN   2015-01-01  1112115.0   
2            France                1.0   1995-01-01  1122795.0   
3       [Worldwide]                NaN   2018-01-01  1720981.0   
4       [Worldwide]                NaN   2016-01-01  1363025.0   

                            artist_mbid      artist_name      origin_name  \
0  d10d6441-dcc1-4202-93bf-0c0acf72913a         Soul Glo     Philadelphia   
1  7b52c77b-1a34-439d-a285-3a7c69cb5b1a      Ben Bennett              NaN   
2  71b8451c-c10a-400e-9544-101f34ab2522  Soixante Étages              NaN   
3  a69efb5f-0b28-4328-8ff0-44d8d6f39755         TedeuzeM  Aix-en-Provence   
4  c941ad72-8b13-4940-8d99-0ed9becad2d7            yzome          Seattle   

   origin_code  group_id_y  
0          3.0         NaN  
1          NaN   1713833.0  
2          NaN   1609358.0  
3          3.0         NaN  
4          3.0         NaN

In [77]:
#Now, let's see what information we have:
df8.origin_name.value_counts()

United States                               81909
United Kingdom                              52863
Japan                                       42326
Germany                                     34079
London                                      26113
France                                      26063
Los Angeles                                 16496
Sweden                                      15467
Italy                                       15210
New York                                    14284
Finland                                     13768
Netherlands                                 10894
Chicago                                      9463
Spain                                        9236
Canada                                       8820
Australia                                    8726
Russia                                       8592
Tokyo                                        8367
Berlin                                       7560
Paris                                        7546


In [78]:
#And the Null values:
df8.isnull().sum(axis=0)

release_id                0
group_id_x                0
release_group             7
credit_id                 0
release_area              0
release_area_name         0
release_code_type    228606
release_year              0
artist_id                 0
artist_mbid               0
artist_name               0
origin_name          252988
origin_code          257417
group_id_y           841903
dtype: int64

In [79]:
len(df8)

1362614

As we mentioned earlier, the information that we would ideally need to represent the origin of music is the artist origin. Unfortunately, we have 252.988 releases without that information.

In order to try to keep as much data as possible, we will fill these rows with the release area name: for these releases, instead of taking into account the artist/band origin, we will input the location where the release was produced.

In [97]:
df8['origin_code'].replace(np.nan, 0, inplace=True) 
df8['release_code_type'].replace(np.nan, 0, inplace=True)

for i in tqdm(range(len(df8))):
    if (df8['origin_code'][i] == 1 and df8['release_code_type'][i] > 1) or df8['origin_code'][i] == 0:
        df8['origin_name'][i] = df8['release_area_name'][i]
        df8['origin_code'][i] = df8['release_code_type'][i]       
        
    else:
        pass

  0%|          | 0/1362614 [00:00<?, ?it/s]/home/ainhoa/anaconda3/envs/kschool/lib/python3.7/site-packages/ipykernel_launcher.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  
/home/ainhoa/anaconda3/envs/kschool/lib/python3.7/site-packages/ipykernel_launcher.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  import sys
100%|██████████| 1362614/1362614 [3:14:32<00:00, 116.74it/s]  


In [98]:
df8.head()

release_id  group_id_x           release_group  credit_id  release_area  \
0     2163750     1962329                            2205562         240.0   
1     1846605     1713833                            1503027         240.0   
2     1714060     1609358   Beaux Soirs De Paris     1324142          73.0   
3     2265346     2042812                   Le 1     2291833         240.0   
4     1772538     1656147            devil jokes     1653884         240.0   

  release_area_name  release_code_type release_year  artist_id  \
0       [Worldwide]                0.0   2014-01-01  1654312.0   
1       [Worldwide]                0.0   2015-01-01  1112115.0   
2            France                1.0   1995-01-01  1122795.0   
3       [Worldwide]                0.0   2018-01-01  1720981.0   
4       [Worldwide]                0.0   2016-01-01  1363025.0   

                            artist_mbid      artist_name      origin_name  \
0  d10d6441-dcc1-4202-93bf-0c0acf72913a         Soul Glo     Philadelphia   
1  7b52c77b-1a34-439d-a285-3a7c69cb5b1a      Ben Bennett      [Worldwide]   
2  71b8451c-c10a-400e-9544-101f34ab2522  Soixante Étages           France   
3  a69efb5f-0b28-4328-8ff0-44d8d6f39755         TedeuzeM  Aix-en-Provence   
4  c941ad72-8b13-4940-8d99-0ed9becad2d7            yzome          Seattle   

   origin_code  group_id_y  
0          3.0         NaN  
1          0.0   1713833.0  
2          1.0   1609358.0  
3          3.0         NaN  
4          3.0         NaN

In [101]:
df8.origin_name.value_counts()

United States                          152550
United Kingdom                          78494
Japan                                   59394
Germany                                 58890
[Worldwide]                             48636
France                                  36161
London                                  26075
Sweden                                  19322
Italy                                   18680
Netherlands                             16545
Los Angeles                             16491
Finland                                 15073
New York                                14259
Canada                                  13883
Spain                                   12902
Australia                               12541
Russia                                  12351
Chicago                                  9463
Tokyo                                    8367
Poland                                   7826
Brazil                                   7749
Berlin                            

Now that we have input the release area information into the origin columns, we cna change back the zero values into NaNs, to be able to analyze them later:

In [102]:
df8['origin_code'].replace(0,np.nan, inplace=True) 
df8['release_code_type'].replace(0,np.nan, inplace=True)

In [103]:
#For the location types, how much volume do we have for each category?
df8.origin_code.value_counts()

1.0    641233
3.0    544416
2.0     74660
5.0     26636
4.0     22369
7.0      2623
6.0       612
Name: origin_code, dtype: int64

In [104]:
#How many Null values do we have now in the origin columns after the change?
df8.isnull().sum(axis=0)

release_id                0
group_id_x                0
release_group             7
credit_id                 0
release_area              0
release_area_name         0
release_code_type    228606
release_year              0
artist_id                 0
artist_mbid               0
artist_name               0
origin_name               0
origin_code           50065
group_id_y           841903
dtype: int64

In [105]:
#We have reduced the Null values in the origin quite a lot with this last change.
#As the above loop took more than 3h to complete, in order to save time we'll save our dataframe in a csv file:
df8.to_csv('dataframe.csv', sep='\t', encoding='utf-8', index=False)

## 5) Adding music genres to our dataframe

According to Musicbrainz's Genre description in https://wiki.musicbrainz.org/Genre:

"Genres are currently supported in MusicBrainz as part of the tag system.

Some tags (the ones in the genre list) are automatically read and presented as genres."

What we want for our visualization is to have, for each release, its main genre and eventually its subgenre. To do so, I have copied Musicbrainz's "genre list" into a csv file. There are 419 elements considered as genres by Musicbrainz but for our study we'll consider them as our subgenres.

I have manually classified all of these subgenres into 14 categories or "Main genres":

- Blues
- Classical
- Country
- Electronic
- Folk
- Heavy Metal
- Hip Hop
- Jazz
- Latin
- Pop
- Punk
- Rythm & Blues (R&B)
- Rock
- Others (This category contains all the subgenres I haven't been able to classify in the previous categories)

Of course, I wasn't familiar with all the genres appearing in the list so, in order to classify those, I looked at their definition in wikipedia and chose the best main genre for them. If no definition was provided by wikipedia, I searched for them in Google and listened to a representative song in order to make a decision.

In [106]:
#Let's see how the genres and subgenres look like:
genres = pd.read_csv('Musicbrainz/Tables_used/genres.csv',sep='\t', encoding='utf-8')
genres.head()

Main_genre        Subgenre
0  Electronic      acid house
1  Electronic       acid jazz
2  Electronic     acid techno
3       Blues  acoustic blues
4        Rock   acoustic rock

As we read before, Musicbrainz's genre list (subgenre for us) is part of their tag system. Let's import the Musicbrainz's "tags" table and try to identify, from its elements, the ones that are genres.

In [107]:
tags = pd.read_csv('Musicbrainz/Tables_used/tags.txt',sep='\t', header=None, engine='c', usecols=[0,1])
tags.columns = ['tag_id','tag_name']
tags.head()

tag_id        tag_name
0      95         finnish
1      23          slovak
2     801            iowa
3       4  groundbreaking
4     130       taiwanese

In [108]:
#How many tags are there?
tags['tag_id'].nunique()

86806

In [109]:
#What do the tags look like?
tags.tag_name.value_counts()

pacific                                                                                                                                                2
herb recordings                                                                                                                                        2
acid folk                                                                                                                                              2
zelimir kulisic                                                                                                                                        2
new age                                                                                                                                                2
west wales                                                                                                                                             2
new age music                                                                     

As we can see, the tags list contains the genres but also other (more subjective) expressions that some users have chosen as representative for the music entity. 

We will add columns to this tags dataframe to distinguish which of them are actually genres/subgenres:

In [110]:
#First, we change the Subgenre column name to tag_name in our genre file, to be able to join both dataframes:
genres.rename(columns={'Subgenre':'tag_name'}, inplace=True)
tags_genres = pd.merge(tags, genres, how='left', on='tag_name')
tags_genres.head()

tag_id        tag_name Main_genre
0      95         finnish        NaN
1      23          slovak        NaN
2     801            iowa        NaN
3       4  groundbreaking        NaN
4     130       taiwanese        NaN

In [111]:
#Did we identify all the 419 genres in our dataframe?
pd.notna(tags_genres['Main_genre']).value_counts()

False    86380
True       426
Name: Main_genre, dtype: int64

In [112]:
#We retrieved 7 more, are there duplicates?
table = tags_genres.dropna(subset=['Main_genre'], axis=0).groupby('tag_name').count()
table[table['tag_id'] != 1]

tag_id  Main_genre
tag_name                            
alternative rock       2           2
hard rock              2           2
hip hop                2           2
indie rock             2           2
new age                2           2
pop punk               2           2
pop rap                2           2
pop rock               2           2
progressive rock       2           2
psychedelic rock       2           2
punk rock              2           2
rock                   2           2

It seems that we have 12 subgenres repeated twice in our tags_genres dataframe. That means they probably have 2 different tag_id's each:

In [113]:
list_duplicates = table[table['tag_id'] != 1].index.tolist()
tags_genres[tags_genres['tag_name'].isin(list_duplicates)]

tag_id          tag_name Main_genre
13595    1182           pop rap    Hip Hop
14217     133         punk rock       Rock
14238     235           hip hop    Hip Hop
14373       7              rock       Rock
15338    1100          pop punk       Punk
15380     618           new age     Others
15534      29  progressive rock       Rock
16100     284        indie rock       Rock
16528     271         hard rock       Rock
16616    1091          pop rock       Rock
17633      20  alternative rock       Rock
17665     709  psychedelic rock       Rock
25722   46401           hip hop    Hip Hop
29712   50463  progressive rock       Rock
30899   52082  alternative rock       Rock
30912   52095        indie rock       Rock
32748   57790           new age     Others
33666   59155          pop punk       Punk
33667   59156         punk rock       Rock
42927   69796         hard rock       Rock
42928   69797          pop rock       Rock
43140   70035           pop rap    Hip Hop
73727  103784              rock       Rock
73732  103789  psychedelic rock       Rock

Indeed, they have two tag_id each so we need to keep both tag_id's in order not to lose information later on.

Musicbrainz provides a table with all the release groups which have been tagged by their users. What we'll do next, is to retrieve those tags and select the ones that are part of the genres list.

In [114]:
release_groups = pd.read_csv('Musicbrainz/Tables_used/release_group.txt',sep='\t', header=None, engine='c', usecols=[0,1,2,3])
release_groups.columns = ['group_id','group_mbid','release_group_name','artist_credit']
release_groups.head()

group_id                            group_mbid  \
0   1964563  f59da930-70ba-4992-a346-7ed2d8e3cda8   
1        12  2b10653e-655d-34fe-9db4-77242d817a17   
2        13  0eac6659-d590-3eb7-8c13-ed8b3fdf4ef7   
3        28  c554da1a-c1aa-30c3-b0bb-44b1b837de33   
4        60  06729175-db17-3443-add7-921739a92762   

            release_group_name  artist_credit  
0                        Wande         627364  
1         Chore of Enchantment             12  
2               The Inevitable             11  
3               Piece and Love             26  
4  Ultimate Alternative Wavers             44

In [115]:
release_groups['group_id'].nunique()

1745126

In [116]:
len(release_groups)

1745126

In [117]:
group_tag = pd.read_csv('Musicbrainz/Tables_used/release_group_tag.txt',sep='\t', header=None, engine='c', usecols=[0,1,2])
group_tag.columns = ['group_id','tag_id','tag_counts']
group_tag.head()

group_id  tag_id  tag_counts
0     93688     150           1
1    906692    1371           1
2    906692    6948           1
3    617615      11           1
4    617615     545           1

In [118]:
#We can now merge the release groups with the tag ids and tag counts:
Table = pd.merge(release_groups, group_tag, how='left', on='group_id')
Table.head()

group_id                            group_mbid    release_group_name  \
0   1964563  f59da930-70ba-4992-a346-7ed2d8e3cda8                 Wande   
1        12  2b10653e-655d-34fe-9db4-77242d817a17  Chore of Enchantment   
2        13  0eac6659-d590-3eb7-8c13-ed8b3fdf4ef7        The Inevitable   
3        13  0eac6659-d590-3eb7-8c13-ed8b3fdf4ef7        The Inevitable   
4        13  0eac6659-d590-3eb7-8c13-ed8b3fdf4ef7        The Inevitable   

   artist_credit   tag_id  tag_counts  
0         627364      NaN         NaN  
1             12  41017.0         2.0  
2             11   1053.0         2.0  
3             11   1230.0         1.0  
4             11     71.0         3.0

In [119]:
#And finally have our release groups associated with their genres:
release_group_genre = pd.merge(Table, tags_genres, how='left', on='tag_id')
release_group_genre.head()

group_id                            group_mbid    release_group_name  \
0   1964563  f59da930-70ba-4992-a346-7ed2d8e3cda8                 Wande   
1        12  2b10653e-655d-34fe-9db4-77242d817a17  Chore of Enchantment   
2        13  0eac6659-d590-3eb7-8c13-ed8b3fdf4ef7        The Inevitable   
3        13  0eac6659-d590-3eb7-8c13-ed8b3fdf4ef7        The Inevitable   
4        13  0eac6659-d590-3eb7-8c13-ed8b3fdf4ef7        The Inevitable   

   artist_credit   tag_id  tag_counts                tag_name Main_genre  
0         627364      NaN         NaN                     NaN        NaN  
1             12  41017.0         2.0  alternative/indie rock        NaN  
2             11   1053.0         2.0                   swing       Jazz  
3             11   1230.0         1.0               dixieland        NaN  
4             11     71.0         3.0                    jazz       Jazz

Let's stop here for a while and check one of the releases that has several genre tags associated. Let's do this with one of the most popular releases of all times: the album "Thriller", by the king of Pop music: Michael Jackson. 

In [120]:
release_group_genre[release_group_genre['group_mbid']=='f32fab67-77dd-3937-addc-9062e28e4c37']

group_id                            group_mbid release_group_name  \
1429052     61656  f32fab67-77dd-3937-addc-9062e28e4c37           Thriller   
1429053     61656  f32fab67-77dd-3937-addc-9062e28e4c37           Thriller   
1429054     61656  f32fab67-77dd-3937-addc-9062e28e4c37           Thriller   
1429055     61656  f32fab67-77dd-3937-addc-9062e28e4c37           Thriller   
1429056     61656  f32fab67-77dd-3937-addc-9062e28e4c37           Thriller   
1429057     61656  f32fab67-77dd-3937-addc-9062e28e4c37           Thriller   
1429058     61656  f32fab67-77dd-3937-addc-9062e28e4c37           Thriller   
1429059     61656  f32fab67-77dd-3937-addc-9062e28e4c37           Thriller   
1429060     61656  f32fab67-77dd-3937-addc-9062e28e4c37           Thriller   
1429061     61656  f32fab67-77dd-3937-addc-9062e28e4c37           Thriller   
1429062     61656  f32fab67-77dd-3937-addc-9062e28e4c37           Thriller   
1429063     61656  f32fab67-77dd-3937-addc-9062e28e4c37           Thriller   
1429064     61656  f32fab67-77dd-3937-addc-9062e28e4c37           Thriller   
1429065     61656  f32fab67-77dd-3937-addc-9062e28e4c37           Thriller   
1429066     61656  f32fab67-77dd-3937-addc-9062e28e4c37           Thriller   
1429067     61656  f32fab67-77dd-3937-addc-9062e28e4c37           Thriller   
1429068     61656  f32fab67-77dd-3937-addc-9062e28e4c37           Thriller   
1429069     61656  f32fab67-77dd-3937-addc-9062e28e4c37           Thriller   
1429070     61656  f32fab67-77dd-3937-addc-9062e28e4c37           Thriller   
1429071     61656  f32fab67-77dd-3937-addc-9062e28e4c37           Thriller   
1429072     61656  f32fab67-77dd-3937-addc-9062e28e4c37           Thriller   
1429073     61656  f32fab67-77dd-3937-addc-9062e28e4c37           Thriller   
1429074     61656  f32fab67-77dd-3937-addc-9062e28e4c37           Thriller   
1429075     61656  f32fab67-77dd-3937-addc-9062e28e4c37           Thriller   

         artist_credit   tag_id  tag_counts                tag_name  \
1429052            519   7282.0         2.0                   vendu   
1429053            519    642.0         2.0                   disco   
1429054            519   7935.0         1.0             discothèque   
1429055            519  24521.0         0.0       80 s and 90 s pop   
1429056            519   1060.0         1.0               dance-pop   
1429057            519    303.0         3.0                    funk   
1429058            519     11.0         0.0              electronic   
1429059            519  41021.0         2.0              club/dance   
1429060            519     76.0         1.0                   dance   
1429061            519  41027.0         3.0        contemporary r&b   
1429062            519   5921.0         1.0               non-music   
1429063            519    978.0         1.0               interview   
1429064            519    609.0         1.0                    soul   
1429065            519      7.0         2.0                    rock   
1429066            519   3534.0         1.0                  motown   
1429067            519     19.0        15.0                     pop   
1429068            519  25536.0         3.0       general pop vocal   
1429069            519   1091.0         3.0                pop rock   
1429070            519  25106.0         1.0       pop internacional   
1429071            519  33221.0         1.0              post-disco   
1429072            519  41023.0         1.0   contemporary pop/rock   
1429073            519   8637.0         3.0                pop soul   
1429074            519  40661.0         4.0                     r&b   
1429075            519  41047.0         7.0  adult contemporary r&b   

         Main_genre  
1429052         NaN  
1429053  Electronic  
1429054         NaN  
1429055         NaN  
1429056  Electronic  
1429057      Others  
1429058  Electronic  
1429059         NaN  
1429060  Electronic  
1429061         R&B  
1429062      Others  
1429063         Na

As we can see, "Pop" is the most used tag for this group so we should keep it as the release's genre.

As music genre is a very subjective feature, in order to be as "objective" as possible, we'll take into consideration the majority of the votes to chose the subgenre and main genre of each release group.

To do so, we will sort the release_group_genre dataframe by number of counts and keep the top tag for each release group.

In [121]:
#We sort by group_id and tag_counts:
release_group_genre.sort_values(['group_id','tag_counts'], ascending=[True,False], inplace=True)
release_group_genre.head()

group_id                            group_mbid release_group_name  \
312152         2  e8bee759-9efc-35c2-93d7-09ace9123467  Eclectic Electric   
312153         2  e8bee759-9efc-35c2-93d7-09ace9123467  Eclectic Electric   
737291         4  8b6f133a-2fdf-3cc2-b84d-1c889adc0939         Blue Lines   
737302         4  8b6f133a-2fdf-3cc2-b84d-1c889adc0939         Blue Lines   
737293         4  8b6f133a-2fdf-3cc2-b84d-1c889adc0939         Blue Lines   

        artist_credit   tag_id  tag_counts                 tag_name  \
312152              1   1186.0         2.0                 acid rap   
312153              1  92310.0         1.0  oldest release group #2   
737291              4   1498.0         7.0                 trip hop   
737302              4     12.0         6.0                downtempo   
737293              4     11.0         5.0               electronic   

        Main_genre  
312152         NaN  
312153         NaN  
737291     Hip Hop  
737302  Electronic  
737293  Electronic

In [122]:
#And now we can drop the duplicate group_ids, keeping the top tags:
release_group_genre.drop_duplicates(subset=['group_id'],keep='first', inplace=True)
release_group_genre.head(20)

group_id                            group_mbid  \
312152          2  e8bee759-9efc-35c2-93d7-09ace9123467   
737291          4  8b6f133a-2fdf-3cc2-b84d-1c889adc0939   
1756939        11  c6fe6a2b-0ed6-3d2c-b9ce-ddd5421a3452   
1              12  2b10653e-655d-34fe-9db4-77242d817a17   
4              13  0eac6659-d590-3eb7-8c13-ed8b3fdf4ef7   
1206877        21  bdd77e94-7917-3aa4-97de-501c53b1d343   
312321         24  555dce82-41bf-397a-a487-997b54bee515   
5              28  c554da1a-c1aa-30c3-b0bb-44b1b837de33   
271            30  2c644807-3b5d-39d4-8c65-dec603bf3f3a   
1089677        37  857c3dff-efec-387e-8e07-5b6bdb746afa   
141            50  fe676d05-f97c-303a-890b-da53c69e5d42   
6              60  06729175-db17-3443-add7-921739a92762   
59             93  78e2be48-6a07-31bf-b85f-3a1093177263   
28240         103  c1bb54cc-751d-300c-ba29-d7502d571c2d   
10            116  4c0130ca-24ea-38e6-acb0-7ec4c8d11945   
208           117  69286fb5-8d5a-3b13-882c-9c3fba8c56d2   
149093        119  3da3cb84-2196-34bf-a67b-f9e4ee22ae76   
194           121  eaefa29b-e02a-3b28-836f-2641670d455b   
312360        142  676e8385-b2de-3cb7-9db0-2aa39021dfe8   
1186954       143  f933cd47-405f-3d0a-97d5-d822428ca2e0   

                              release_group_name  artist_credit   tag_id  \
312152                         Eclectic Electric              1   1186.0   
737291                                Blue Lines              4   1498.0   
1756939                                      Hot             11     71.0   
1                           Chore of Enchantment             12  41017.0   
4                                 The Inevitable             11     71.0   
1206877  The Best of the Art of Noise: Art Works             20     11.0   
312321            Emusic: The Extreme Collection              1      NaN   
5                                 Piece and Love             26      NaN   
271                                    Let It Be             28  41017.0   
1089677                                Liz Story        1097111    507.0   
141                            Live Through This             38    175.0   
6                    Ultimate Alternative Wavers             44      7.0   
59                                           Dry           9044    284.0   
28240                                  Rid of Me           9044    284.0   
10                              The Glass Intact             68      NaN   
208                                      Distant             68      NaN   
149093                           Call the Doctor        1301647      NaN   
194                                 The Hot Rock        1301647      NaN   
312360   Universal Madness (Live in Los Angeles)             85      7.0   
1186954                            Dub in Fusion             86      NaN   

         tag_counts                tag_name  Main_genre  
312152          2.0                acid rap         NaN  
737291          7.0                trip hop     Hip Hop  
1756939         3.0                    jazz        Jazz  
1               2.0  alternative/indie rock         NaN  
4               3.0                    jazz        Jazz  
1206877         2.0              electronic  Electronic  
312321          NaN                     NaN         NaN  
5               NaN                     NaN         NaN  
271             1.0  alternative/indie rock         NaN  
1089677         1.0                   piano         NaN  
141             4.0                  grunge        Rock  
6               1.0                    rock        Rock  
59              4.0              indie rock        Rock  
28240           4.0              indie rock        Rock  
10              NaN                     NaN         NaN  
208             NaN                     NaN         NaN  
149093          NaN                     NaN         NaN  
194             NaN                     NaN         NaN  
312360          1.0                    rock        Rock  
1186954     

What we want now is to combine our main dataframe (which we exported at the end of part 4 of this notebook) with this new genre information we just retrieved:

In [123]:
#We open our main dataframe:
dataframe = pd.read_csv('dataframe.csv',sep='\t', encoding='utf-8')
dataframe.head()

release_id  group_id_x           release_group  credit_id  release_area  \
0     2163750     1962329                            2205562         240.0   
1     1846605     1713833                            1503027         240.0   
2     1714060     1609358   Beaux Soirs De Paris     1324142          73.0   
3     2265346     2042812                   Le 1     2291833         240.0   
4     1772538     1656147            devil jokes     1653884         240.0   

  release_area_name  release_code_type release_year  artist_id  \
0       [Worldwide]                NaN   2014-01-01  1654312.0   
1       [Worldwide]                NaN   2015-01-01  1112115.0   
2            France                1.0   1995-01-01  1122795.0   
3       [Worldwide]                NaN   2018-01-01  1720981.0   
4       [Worldwide]                NaN   2016-01-01  1363025.0   

                            artist_mbid      artist_name      origin_name  \
0  d10d6441-dcc1-4202-93bf-0c0acf72913a         Soul Glo     Philadelphia   
1  7b52c77b-1a34-439d-a285-3a7c69cb5b1a      Ben Bennett      [Worldwide]   
2  71b8451c-c10a-400e-9544-101f34ab2522  Soixante Étages           France   
3  a69efb5f-0b28-4328-8ff0-44d8d6f39755         TedeuzeM  Aix-en-Provence   
4  c941ad72-8b13-4940-8d99-0ed9becad2d7            yzome          Seattle   

   origin_code  group_id_y  
0          3.0         NaN  
1          NaN   1713833.0  
2          1.0   1609358.0  
3          3.0         NaN  
4          3.0         NaN

# SEGUIR DESDE AQUI

If we look at the above table, the first line for instance, has the tag "acid rap" associated but this tag isn't considered as a genre by Musicbrainz so, if we decide not to take into consideration this information, we would lose many items for our visualization:

In [46]:
release_group_genre['group_id'].nunique()

1745126

In [56]:
#How many release groups did we retrieved the Main genre for?
pd.notna(release_group_genre['Main_genre']).value_counts()

False    1712671
True      323011
Name: Main_genre, dtype: int64

In [60]:
#Wah are the tag names that don't have a genre?
genreless = release_group_genre[pd.notna(release_group_genre.tag_name) & pd.isnull(release_group_genre.Main_genre)]
genreless.head()

group_id                            group_mbid  \
1         12  2b10653e-655d-34fe-9db4-77242d817a17   
3         13  0eac6659-d590-3eb7-8c13-ed8b3fdf4ef7   
7         60  06729175-db17-3443-add7-921739a92762   
16       454  c997762b-9719-3db3-8681-4e8731324cdf   
19       454  c997762b-9719-3db3-8681-4e8731324cdf   

             release_group_name  artist_credit   tag_id  tag_counts  \
1          Chore of Enchantment             12  41017.0         2.0   
3                The Inevitable             11   1230.0         1.0   
7   Ultimate Alternative Wavers             44  23174.0         1.0   
16           Solitude/Solitaire            327   5949.0         0.0   
19           Solitude/Solitaire            327   1085.0         2.0   

                  tag_name Main_genre  
1   alternative/indie rock        NaN  
3                dixieland        NaN  
7          rock_indie rock        NaN  
16                  hi nrg        NaN  
19      adult contemporary        NaN

In [61]:
len(genreless)

154656

As we can see above, some of the tags that don't have a Main genre associated could be easily classified (for instance: "alternative/indie rock", or "rock_indie rock"). 

What I will do now is to group this genreless subset by tag_name, export it to a csv file and manually classify the tags I can, using the same criteria I did before.

In [74]:
genreless_grouped = genreless.groupby('tag_name').count().reset_index()[['tag_name','tag_counts','Main_genre']].copy()
genreless_grouped.to_csv('genreless.csv', sep='\t', index=None, encoding='utf-8')

In [48]:
type(release_genre[release_genre['release_id']==8340])

pandas.core.frame.DataFrame

In [24]:
tags[tags['tag_id']==7]

tag_id tag_name      b
14373       7     rock  65222

In [9]:
tags[tags['tag_id']==40899]

tag_id     tag_name  b
19638   40899  rock & roll  0

In [17]:
tags[tags['tag_id']==714]

tag_id tag_name    b
16527     714  britpop  236

In [18]:
artist_tag = pd.read_csv('Musicbrainz/Tables_used/artist_tag.txt',sep='\t', header=None, engine='c', usecols=[0,1,2])
artist_tag.columns = ['artist_id','tag_id','tag_count']
artist_tag.head()

artist_id  tag_id  tag_count
0     468800      29          2
1     522545   63294          1
2      31390     173          1
3     108404     271          1
4     108404       7          1